In [10]:
!pip install seaborn evidently

Defaulting to user installation because normal site-packages is not writeable


In [2]:
import matplotlib.pyplot as plt
import numpy as np

# from sklearnex import patch_sklearn
# patch_sklearn()

from matplotlib import rc
import matplotlib.ticker as tkr
import matplotlib.dates as mdates
from datetime import datetime, timedelta
from matplotlib.colors import ListedColormap
import seaborn as sns
sns.set_style("whitegrid")
sns.set_style("ticks")
import scipy.io as sio

import pandas as pd

import sys

%matplotlib inline

from matplotlib.pylab import rcParams
rcParams['figure.figsize'] = 10, 8
rcParams['figure.dpi'] = 90

%config InlineBackend.figure_format = 'retina'

import warnings
warnings.filterwarnings('ignore')

In [3]:
from sklearn import linear_model
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from matplotlib.pylab import rc, plot
import seaborn as sns
from sklearn.preprocessing import LabelEncoder, OneHotEncoder
from sklearn.model_selection import cross_val_score
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, RandomForestRegressor
from sklearn.metrics import precision_recall_curve, classification_report
from sklearn.model_selection import train_test_split
from pandas import read_csv, DataFrame
from sklearn.metrics import roc_curve
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier
# from sklearn.cross_validation import train_test_split
from sklearn.naive_bayes import GaussianNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.decomposition import PCA
# import ml_metrics, string, re, pylab as pl
from sklearn.svm import LinearSVC
from sklearn.metrics import mean_squared_error, r2_score, median_absolute_error, explained_variance_score, accuracy_score
from sklearn import svm
from sklearn.neural_network import MLPRegressor

In [4]:
dfi = pd.read_csv('/home/sir/farmy/ch.farmy.scinode/development/9631-update/farmy_bags_forecast_v2.csv')
dfi = dfi[dfi.bags_used<10]
dfi = dfi[dfi.bags_used>0]
dfi = dfi[(dfi.total_weight<5e4)]
# dfi = dfi[(dfi.hub_id == 4)]
dfi.fillna(0.0, inplace=True)

In [5]:
import mlflow
from hyperopt.pyll import scope

mlflow.set_tracking_uri("sqlite:////home/sir/farmy/ch.farmy.scinode/development/9631-update/mlflow.db")
mlflow.set_experiment("bags-10.67.2")

<Experiment: artifact_location='/home/sir/farmy/ch.farmy.scinode/development/9631-update/mlruns/12', creation_time=1716758005245, experiment_id='12', last_update_time=1716758958550, lifecycle_stage='active', name='bags-10.67.2', tags={}>

In [6]:
extra_features = list() + ['day_of_week']   + ['number_of_week'] + ['delivery_hour']    # + ['day_of_year']
features = list(dfi.columns[0:-8]) + extra_features
# features

In [7]:
len(features)

67

In [12]:
df_enriched = dfi.copy()

df_enriched['delivery_time'] = pd.to_datetime(dfi['delivery_time'], utc=True)

In [15]:
from evidently import ColumnMapping

from evidently.report import Report
from evidently.metrics.base_metric import generate_column_metrics
from evidently.metric_preset import DataDriftPreset, TargetDriftPreset
from evidently.metrics import *

from evidently.test_suite import TestSuite
from evidently.tests.base_test import generate_column_tests
from evidently.test_preset import DataStabilityTestPreset, NoTargetPerformanceTestPreset
from evidently.tests import *

In [18]:
report = Report(metrics=[DataDriftPreset()])

reference = df_enriched[(df_enriched['delivery_time'] > start_date) & (df_enriched['delivery_time'] < end_date)]
current = df_enriched[(df_enriched['delivery_time'] >= end_date)]

# Verify non-empty datasets for the report
if reference.empty:
    raise ValueError("The reference dataset is empty. Please check the date range.")
if current.empty:
    raise ValueError("The current dataset is empty. Please check the date range.")

# Ensure no missing values and correct data types for correlation calculation
num_columns = reference.select_dtypes(include=[np.number]).columns.tolist()
reference = reference[num_columns].dropna()
current = current[num_columns].dropna()

if reference.empty or current.empty:
    raise ValueError("The datasets must contain numeric columns without missing values for correlation calculation.")

# Run the report
report.run(reference_data=reference, current_data=current)

# Show the report inline
# report.show(mode='inline')
str(report.as_dict())

"{'metrics': [{'metric': 'DatasetDriftMetric', 'result': {'drift_share': 0.5, 'number_of_columns': 71, 'number_of_drifted_columns': 2, 'share_of_drifted_columns': 0.028169014084507043, 'dataset_drift': False}}, {'metric': 'DataDriftTable', 'result': {'number_of_columns': 71, 'number_of_drifted_columns': 2, 'share_of_drifted_columns': 0.028169014084507043, 'dataset_drift': False, 'drift_by_columns': {'Baby & Kind (cold VU)': {'column_name': 'Baby & Kind (cold VU)', 'column_type': 'num', 'stattest_name': 'Wasserstein distance (normed)', 'stattest_threshold': 0.1, 'drift_score': 0.029992184589236026, 'drift_detected': False, 'current': {'small_distribution': {'x': [0.0, 1.2, 2.4, 3.5999999999999996, 4.8, 6.0, 7.199999999999999, 8.4, 9.6, 10.799999999999999, 12.0], 'y': [0.8279551136693994, 0.001598930170358742, 0.0007267864410721556, 0.0011628583057154485, 0.0007267864410721552, 0.0007267864410721557, 0.0, 0.0, 0.00014535728821443115, 0.00029071457642886186]}}, 'reference': {'small_distri

In [8]:
df_enriched['day_of_year'] = df_enriched['delivery_time'].dt.dayofyear
df_enriched['day_of_week'] = df_enriched['delivery_time'].dt.dayofweek
df_enriched['number_of_week'] = df_enriched['delivery_time'].dt.isocalendar().week # .dt.week #
df_enriched['delivery_hour'] = df_enriched['delivery_time'].dt.hour


# 3. Filter the data for the given date range
timezone = df_enriched['delivery_time'].iloc[0].tzinfo
start_date = pd.to_datetime('2022-09-01').tz_localize(timezone)
end_date = pd.to_datetime('2023-09-01').tz_localize(timezone)
df_filtered = df_enriched[(df_enriched['delivery_time'] > start_date) & (df_enriched['delivery_time'] < end_date)]

# 4. Add 'day_of_year' and 'day_of_week' columns to the filtered data (will only execute if df_filtered is not empty)
if df_filtered.empty:
    print("filtered no data!")

# train = data.sample(frac=0.95)
# df_test = df_filtered.loc[~df_filtered.index.isin(df_filtered.index)]

sep_test = df_enriched[(df_enriched['delivery_time'] > end_date)] # | (dfi['delivery_time'] < start_date)]


In [67]:
import xgboost as xgb
from joblib import dump, load
from sklearn.model_selection import train_test_split

In [68]:
!pip install hyperopt

In [69]:
mlflow.xgboost.autolog()
df_filtered[features]

Sets & weiteres (normal VU)  Sets & weiteres (normal weight)  \
450                               0                              0.0   
453                               0                              0.0   
454                               1                           2000.0   
455                               0                              0.0   
460                               0                              0.0   
...                             ...                              ...   
304456                            0                              0.0   
304457                            0                              0.0   
304458                            0                              0.0   
304469                            0                              0.0   
304487                            0                              0.0   

        Sets & weiteres (cold VU)  Sets & weiteres (cold weight)  \
450                             0                            0.0   
453                             0                            0.0   
454                             0                            0.0   
455                             0                            0.0   
460                             0                            0.0   
...                           ...                            ...   
304456                          1                         5000.0   
304457                          0                            0.0   
304458                          1                         5000.0   
304469                          0                            0.0   
304487                          0                            0.0   

        Sets & weiteres (frozen VU)  Sets & weiteres (frozen weight)  \
450                               0                              0.0   
453                               0                              0.0   
454                               0                              0.0   
455                               0                              0.0   
460                               0                              0.0   
...                             ...                              ...   
304456                            0                              0.0   
304457                            0                              0.0   
304458                            0                              0.0   
304469                            0                              0.0   
304487                            0                              0.0   

        Früchte & Gemüse (normal VU)  Früchte & Gemüse (normal weight)  \
450                                0                               0.0   
453                                0                               0.0   
454                                0                               0.0   
455                                0                               0.0   
460                                0                               0.0   
...                              ...                               ...   
304456                             0                               0.0   
304457                             0                               0.0   
304458                             0                               0.0   
304469                             0                               0.0   
304487                             0                               0.0   

        Früchte & Gemüse (cold VU)  Früchte & Gemüse (cold weight)  ...  \
450                             13                          4000.0  ...   
453                              9                          3355.0  ...   
454                              0                             0.0  ...   
455                              0                             0.0  ...   
460                             32                         12310.0  ...   
...                            ...                             ...  ...   
304456                           0             

In [70]:
from hyperopt import fmin, tpe, hp, Trials, STATUS_OK
import mlflow
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import train_test_split
import numpy as np


def train_model(target_column, hub_id, features):
    def objective(params):
        with mlflow.start_run():
            #params['n_estimators'] = int(params['n_estimators'])  # hyperopt returns floats
            #params['max_depth'] = int(params['max_depth'])        # hyperopt returns floats
#            params['min_samples_leaf'] = int(params['min_samples_leaf'])        # hyperopt returns floats
#            params['min_samples_split'] = int(params['min_samples_split'])        # hyperopt returns floats

            print(params)
            mlflow.log_params(params)
            mlflow.set_tag('features', str(len(features)))
            # model = RandomForestRegressor(**params)
            X_train = train[features].values
            y_train = train[target].values
            X_val = test[features].values
            y_val = test[target].values
            train_matrix = xgb.DMatrix(X_train, label=y_train)
            valid_matrix = xgb.DMatrix(X_val, label=y_val)
            model = xgb.train(
                params=params,
                # device="cuda", tree_method="gpu_hist",
                dtrain=train_matrix,
                num_boost_round=1000,
                evals=[(valid_matrix, 'validation')],
                early_stopping_rounds=50
            )
            y_pred = model.predict(valid_matrix)
            rmse = mean_squared_error(y_val, y_pred, squared=False)
            mlflow.log_metric("rmse", rmse)

            #y_test = model.predict(test[features].values).flatten()
            #mse_test = mean_squared_error(test[target].values.flatten(), np.around(y_test))
            #print("prediction for Test slice:  {:.5f}".format(mse_test))
            #mlflow.log_metric("mse_test", mse_test)

            
            #y_test = model.predict(sep_test[features].values).flatten()
            #mse_sep = mean_squared_error(sep_test[target].values.flatten(), np.around(y_test))
            #print("prediction for Sept slice:  {:.5f}".format(mse_sep))
            #mlflow.log_metric("mse_sep", mse_sep)

            #y_train = model.predict(train[features].values).flatten()
            #mse_train = mean_squared_error(train[target].values.flatten(), np.around(y_train))
            #print("prediction for train slice: {:.5f} (should be smallest but not differ a lot from test MSE)".format(mse_train))
            #mlflow.log_metric("mse_train", mse_train)

        return {'loss': rmse, 'status': STATUS_OK}

            
            # model = xgb.XGBRegressor(**params, device="cuda", tree_method="gpu_hist")
            #model = xgb.train(**params, device="cuda", tree_method="gpu_hist")
                             
                             
            #model.fit(train[features].values, train[target].values)
            

            #return {'loss': mse_test, 'status': STATUS_OK}

    #mlflow.log_param("column", target_column)
    #mlflow.log_param("hub_id", hub_id)
    target_column_name = target_column+'_used'
    forecast_column_name = target_column_name+'_forecast'

    columns = features + [target_column_name] + [forecast_column_name]
    data = df_filtered[df_filtered.hub_id == hub_id][columns]
    data.dropna(inplace=True)
    target = [target_column_name]

    train, test = train_test_split(data, test_size=0.3, random_state=42)


    space = {
        'objective': hp.choice('objective', ["reg:squarederror","reg:linear"]), 
        'random_state': 42, 
        'colsample_bytree': hp.uniform('colsample_bytree', 0.5, 1), # 0.707
        'gamma': hp.uniform('gamma', 0.2, 0.35), # =0.323, 
        'learning_rate': hp.loguniform('learning_rate', np.log(0.005), np.log(0.02)), # learning_rate=0.024, 
        'max_depth':  scope.int(hp.quniform('max_depth', 8, 13, 1)), # max_depth=9, 
        'n_estimators': scope.int(hp.quniform('n_estimators', 700, 1400, 100)), # n_estimators=800, 
        'subsample': hp.uniform('subsample', 0.4, 1) # =0.9991,
        #'verbosity': 1
    }

    space = {
        # 'booster': hp.choice('booster', ['gbtree', 'gblinear']),
        'objective': hp.choice('objective', ["reg:squarederror", "reg:linear"]),
        'random_state': 42,
        'colsample_bytree': hp.uniform('colsample_bytree', 0.5, 1),
        'gamma': hp.uniform('gamma', 0.2, 0.35),
        'learning_rate': hp.loguniform('learning_rate', np.log(0.005), np.log(0.03)),
        'max_depth': scope.int(hp.quniform('max_depth', 8, 13, 1)),
        'n_estimators': scope.int(hp.quniform('n_estimators', 700, 1400, 100)),
        'subsample': hp.uniform('subsample', 0.4, 1),
        'verbosity': 1
    }
    
    trials = Trials()
    best = fmin(fn=objective,
                space=space,
                algo=tpe.suggest,
                max_evals=50,
                trials=trials)

    #best['n_estimators'] = int(best['n_estimators'])
    #best['max_depth'] = int(best['max_depth'])
    #best['min_samples_leaf'] = int(best['min_samples_leaf'])        # hyperopt returns floats
    #best['min_samples_split'] = int(best['min_samples_split'])        # hyperopt returns floats

    model = xgb.XGBRegressor(**best, device="cuda", tree_method="gpu_hist")
                                  
    with mlflow.start_run():
        mlflow.log_params(best)

        model.fit(train[features].values, train[target].values)

        print("Mean Squared Error between {} and:".format(target_column))
        y_forecast = data[forecast_column_name].values.flatten()
        mse_forecast = mean_squared_error(data[target].values.flatten(), y_forecast)
        print("forecast from DB:           {:.5f} (should be worst)".format(mse_forecast))
        mlflow.log_metric("mse_old", mse_forecast)

        y_test = model.predict(test[features].values).flatten()
        mse_test = mean_squared_error(test[target].values.flatten(), np.around(y_test))
        print("prediction for test slice:  {:.5f}".format(mse_test))

        mlflow.log_metric("mse_test", mse_test)

        y_test = model.predict(sep_test[features].values).flatten()
        mse_sep = mean_squared_error(sep_test[target].values.flatten(), np.around(y_test))
        #print("prediction for Sept slice:  {:.5f}".format(mse_sep))
        #mlflow.log_metric("mse_sep", mse_sep)

        y_train = model.predict(train[features].values).flatten()
        mse_train = mean_squared_error(train[target].values.flatten(), np.around(y_train))
        print("prediction for train slice: {:.5f} (should be smallest but not differ a lot from test MSE)".format(mse_train))
        mlflow.log_metric("mse_train", mse_train)

    return model


In [71]:
def train_model_old(target_column, hub_id, features):
    with mlflow.start_run():
        mlflow.log_param("column", target_column)
        mlflow.log_param("hub_id", hub_id)
        target_column_name = target_column+'_used'
        forecast_column_name = target_column_name+'_forecast'

        columns = features + [target_column_name] + [forecast_column_name]
        data = df_filtered[df_filtered.hub_id==hub_id][columns]
        data.dropna(inplace=True)
        target = [target_column_name]

        # train = data.sample(frac=0.95)
        # test = data.loc[~data.index.isin(train.index)]

        train, test = train_test_split(data, test_size=0.3, random_state=42)

        if (target_column == "deep_frozen_bags"):
            params = { 'bootstrap': False, 
            'ccp_alpha': 0.0, 
            'criterion': 'squared_error', 
            'max_depth': 30, 
            'max_features': 'sqrt', 
            'max_leaf_nodes': None, 
            'max_samples': None, 
            'min_impurity_decrease': 0.0, 
            'min_samples_leaf': 2, 
            'min_samples_split': 10, 
            'min_weight_fraction_leaf': 0.0, 
            'n_estimators': 1600, 
            'n_jobs': 6, 
            'oob_score': False, 
            'random_state': 42, 
            'verbose': 0, 
            'warm_start': False
            }

            model = RandomForestRegressor(**params)
            mlflow.log_params(params)
        #else:
        #    model = xgb.XGBRegressor(# device="cuda", tree_method="gpu_hist",
        #                             objective="reg:squarederror", random_state=42, 
        #                             colsample_bytree=0.707, gamma=0.323, 
        #                             learning_rate=0.024, max_depth=9, n_estimators=800, 
        #                             subsample=0.9991,
        #                             verbosity=0)

        model.fit(train[features].values, train[target].values)


        print("Mean Squared Error between {} and:".format(target_column))
        y_forecast = data[forecast_column_name].values.flatten()
        mse_forecast = mean_squared_error(data[target].values.flatten(), y_forecast)
        print("forecast from DB:           {:.5f} (should be worst)".format(mse_forecast))
        mlflow.log_metric("mse_old", mse_forecast)
        
        y_test = model.predict(test[features].values).flatten()
        mse_test = mean_squared_error(test[target].values.flatten(), np.around(y_test))
        print("prediction for test slice:  {:.5f} ({:.2f}% improvement)".format(mse_test, (mse_forecast-mse_test)/mse_test*100))

        mlflow.log_metric("mse_test", mse_test)
        
        y_test = model.predict(sep_test[features].values).flatten()
        mse_sep = mean_squared_error(sep_test[target].values.flatten(), np.around(y_test))
        print("prediction for Sept slice:  {:.5f} ({:.2f}% improvement)".format(mse_sep, (mse_forecast-mse_sep)/mse_sep*100))
        mlflow.log_metric("mse_sep", mse_sep)
        
        y_train = model.predict(train[features].values).flatten()
        mse_train = mean_squared_error(train[target].values.flatten(), np.around(y_train))
        print("prediction for train slice: {:.5f} (should be smallest but not differ a lot from test MSE)".format(mse_train))
        mlflow.log_metric("mse_train", mse_train)
        
        # dump(model, 'new/{}_model_v3_hub_{}.joblib'.format(target_column, hub_id), compress=True)
        return model

In [72]:
print('{}-{} for {}'.format(start_date, end_date, extra_features))
target_columns = [ 'bags' ] # 'deep_frozen_bags' ] # , 'cold_bags', 'bags']
for hub_id in [1]:
    print("hub ",hub_id)
    for target_column in target_columns:
        model = train_model(target_column, hub_id, features)
        print(model.get_params())

2022-09-01 00:00:00+00:00-2023-09-01 00:00:00+00:00 for ['day_of_week', 'number_of_week', 'delivery_hour']
hub  1
{'colsample_bytree': 0.9870420002952984, 'gamma': 0.2130226916764326, 'learning_rate': 0.013711451340722968, 'max_depth': 13, 'n_estimators': 900, 'objective': 'reg:linear', 'random_state': 42, 'subsample': 0.8657224179382892, 'verbosity': 1}
[0]	validation-rmse:1.62148                                                     
[1]	validation-rmse:1.60699                                                     
[2]	validation-rmse:1.59278                                                     
[3]	validation-rmse:1.57892                                                     
[4]	validation-rmse:1.56536                                                     
[5]	validation-rmse:1.55190                                                     
[6]	validation-rmse:1.53879                                                     
[7]	validation-rmse:1.52580                                                 

[197]	validation-rmse:0.88297                                                   
[198]	validation-rmse:0.88264                                                   
[199]	validation-rmse:0.88227                                                   
[200]	validation-rmse:0.88201                                                   
[201]	validation-rmse:0.88170                                                   
[202]	validation-rmse:0.88144                                                   
[203]	validation-rmse:0.88115                                                   
[204]	validation-rmse:0.88089                                                   
[205]	validation-rmse:0.88065                                                   
[206]	validation-rmse:0.88038                                                   
[207]	validation-rmse:0.88011                                                   
[208]	validation-rmse:0.87988                                                   
[209]	validation-rmse:0.8796

[399]	validation-rmse:0.85922                                                   
[400]	validation-rmse:0.85916                                                   
[401]	validation-rmse:0.85912                                                   
[402]	validation-rmse:0.85906                                                   
[403]	validation-rmse:0.85901                                                   
[404]	validation-rmse:0.85897                                                   
[405]	validation-rmse:0.85889                                                   
[406]	validation-rmse:0.85882                                                   
[407]	validation-rmse:0.85876                                                   
[408]	validation-rmse:0.85873                                                   
[409]	validation-rmse:0.85869                                                   
[410]	validation-rmse:0.85860                                                   
[411]	validation-rmse:0.8585

[601]	validation-rmse:0.85382                                                   
[602]	validation-rmse:0.85381                                                   
[603]	validation-rmse:0.85377                                                   
[604]	validation-rmse:0.85377                                                   
[605]	validation-rmse:0.85377                                                   
[606]	validation-rmse:0.85377                                                   
[607]	validation-rmse:0.85376                                                   
[608]	validation-rmse:0.85374                                                   
[609]	validation-rmse:0.85372                                                   
[610]	validation-rmse:0.85369                                                   
[611]	validation-rmse:0.85368                                                   
[612]	validation-rmse:0.85368                                                   
[613]	validation-rmse:0.8536

[803]	validation-rmse:0.85196                                                   
[804]	validation-rmse:0.85197                                                   
[805]	validation-rmse:0.85196                                                   
[806]	validation-rmse:0.85195                                                   
[807]	validation-rmse:0.85195                                                   
[808]	validation-rmse:0.85194                                                   
[809]	validation-rmse:0.85194                                                   
[810]	validation-rmse:0.85193                                                   
[811]	validation-rmse:0.85190                                                   
[812]	validation-rmse:0.85191                                                   
[813]	validation-rmse:0.85190                                                   
[814]	validation-rmse:0.85189                                                   
[815]	validation-rmse:0.8519

...

[314]	validation-rmse:0.92168                                                   
[315]	validation-rmse:0.92133                                                   
[316]	validation-rmse:0.92090                                                   
[317]	validation-rmse:0.92055                                                   
[318]	validation-rmse:0.92015                                                   
[319]	validation-rmse:0.91981                                                   
[320]	validation-rmse:0.91946                                                   
[321]	validation-rmse:0.91904                                                   
[322]	validation-rmse:0.91870                                                   
[323]	validation-rmse:0.91833                                                   
[324]	validation-rmse:0.91800                                                   
[325]	validation-rmse:0.91766                                                   
[326]	validation-rmse:0.9173

[516]	validation-rmse:0.87869                                                   
[517]	validation-rmse:0.87857                                                   
[518]	validation-rmse:0.87847                                                   
[519]	validation-rmse:0.87833                                                   
[520]	validation-rmse:0.87818                                                   
[521]	validation-rmse:0.87805                                                   
[522]	validation-rmse:0.87795                                                   
[523]	validation-rmse:0.87786                                                   
[524]	validation-rmse:0.87770                                                   
[525]	validation-rmse:0.87760                                                   
[526]	validation-rmse:0.87743                                                   
[527]	validation-rmse:0.87730                                                   
[528]	validation-rmse:0.8771

[718]	validation-rmse:0.86191                                                   
[719]	validation-rmse:0.86188                                                   
[720]	validation-rmse:0.86180                                                   
[721]	validation-rmse:0.86172                                                   
[722]	validation-rmse:0.86166                                                   
[723]	validation-rmse:0.86158                                                   
[724]	validation-rmse:0.86150                                                   
[725]	validation-rmse:0.86146                                                   
[726]	validation-rmse:0.86143                                                   
[727]	validation-rmse:0.86140                                                   
[728]	validation-rmse:0.86137                                                   
[729]	validation-rmse:0.86133                                                   
[730]	validation-rmse:0.8612

[920]	validation-rmse:0.85427                                                   
[921]	validation-rmse:0.85422                                                   
[922]	validation-rmse:0.85419                                                   
[923]	validation-rmse:0.85416                                                   
[924]	validation-rmse:0.85412                                                   
[925]	validation-rmse:0.85409                                                   
[926]	validation-rmse:0.85407                                                   
[927]	validation-rmse:0.85405                                                   
[928]	validation-rmse:0.85401                                                   
[929]	validation-rmse:0.85398                                                   
[930]	validation-rmse:0.85397                                                   
[931]	validation-rmse:0.85394                                                   
[932]	validation-rmse:0.8539

TypeError: 'numpy.float64' object cannot be interpreted as an integer